In [3]:
magma_dir = '/home/marco/epfl/magma/'

### **Config**

In [4]:
import os
import sys

sys.path.insert(0, magma_dir)
import config

In [5]:
MODEL = 'bart'

RE_SPLITTER = '\n'              # do we split sentences of paragraphs?
                                # use '\.(?!\d)|\n' or '\n', respectively

TOKEN_MAX_LEN = 99              # max length of a word
PARA_MIN_LENGTH = 2             # minimum length for a sentence or
                                # a paragraph, in tokens

RECALL_THRESHOLD = 0.7

# Output path
OUTPUT_PATH = magma_dir+'datasets/karger_books_para/'+MODEL+'/'
if not os.path.exists(OUTPUT_PATH):
    os.makedirs(OUTPUT_PATH)

### **Init**

In [6]:
import matplotlib.pyplot as plt
import numpy as np
import torch
import re
import pandas as pd
import gensim
from tqdm import tqdm
tqdm.pandas()

if 'pegasus' in MODEL:
    from transformers import PegasusTokenizer
    tokenizer =\
        PegasusTokenizer.from_pretrained('google/pegasus-large')
elif 'bart' in MODEL:
    from transformers import BartTokenizer
    tokenizer =\
        BartTokenizer.from_pretrained('facebook/bart-large-cnn')

### **Karger Books Base Dataset**

In [9]:
base_dataset = magma_dir+'datasets/karger_books_base/df.csv'
df = pd.read_csv(base_dataset)
df = df.set_index(['book', 'chapter', 'section', 'subsection'])
df.bullets = df.bullets.map(eval, na_action='ignore')

## **Paragraph Assign Bullets**

### **Preprocessing**

#### Preprocessing

* Split based on RE_SPLITTER
* Explode the dataset
* Remove unwanted chars at beginning or end of sentence
* Remove multiple spaces
* Remove long words (> TOKEN_MAX_LEN chars)
* Remove short sentences / paragraphs (< PARA_MIN_LENGTH tokens)

In [10]:
# Split in sentences / paragraphs based on RE_SPLITTER
df.text =\
    df.text.map(lambda x: [p.strip() for p in re.split(RE_SPLITTER, x) if p!=''],
                na_action='ignore')
    
# explode to get one row for each paragraph /sentence
df = df.explode('text')
df = df.rename(columns={'text': 'para'})
df = df.dropna()

# Remove unwanted chars at beginning or end of sentence
df.para = df.para.map(lambda p: p.lstrip('.,;:-)] \n'))
df.para = df.para.map(lambda p: p.rstrip('.,;:-([ \n'))

# Remove multiple spaces
df.para = df.para.map(lambda p:
    re.sub('\s+', ' ', p).strip())

# Remove long words (> TOKEN_MAX_LEN chars)
def para2words(para):
    return gensim.utils.simple_preprocess(
        para, deacc=True, max_len=TOKEN_MAX_LEN)
df['para_proc'] = df.para.map(para2words)

# Remove short sentences / paragraphs (< PARA_MIN_LENGTH tokens)
df.loc[df.para_proc.map(len) <\
    PARA_MIN_LENGTH, 'para_proc'] = np.nan

df = df.dropna()

### **Prepare Paragraphs**

In [11]:
df.para = df.para.map(lambda p: p+'.')
df = df.drop(columns='para_proc')
df = df.explode('bullets')

In [12]:
df['para_num_tokens'] = df.para.map(lambda p: len(tokenizer.tokenize(p)))
df['bullets_num_tokens'] = df.bullets.map(lambda b: len(tokenizer.tokenize(b)))

df['compression_ratio'] = df.bullets_num_tokens / df.para_num_tokens

### **Evaluate ROUGE recall**

In [13]:
from datasets import load_metric
metric = load_metric("rouge")

rouge_res =\
    df[['para', 'bullets']]\
    .progress_apply(lambda row:
    metric.compute(
        predictions = [row[0]],
        references = [row[1]],
        rouge_types = config.ROUGE_TYPES,
        use_agregator = False), axis=1)
    
for r in config.ROUGE_TYPES:
    df[r+'_recall'] =\
        rouge_res.map(lambda score: score[r][0][1])

100%|██████████| 114574/114574 [05:20<00:00, 357.91it/s]


### **Assign Bullets to ONE Paragraph and Expand**

In [14]:
def assign_highest_recall_para(df):
    df_one_para = df.copy()

    df_one_para['best_match'] = False

    for idx, para  in df_one_para.groupby('bullets').apply(
        lambda g: g.iloc[g[config.ROUGE_TYPE_RECALL].argmax()]).para.iteritems():
        
        df_one_para.loc[\
            (df_one_para['bullets'] == idx) &\
            (df_one_para['para'] == para), 'best_match'] = True
    
    return df_one_para

df_one_para = assign_highest_recall_para(df)

In [15]:
para_too_short = df_one_para[(df_one_para['compression_ratio'] >= config.MAX_RATIO) & df_one_para['best_match']]
print('Percentage of paragraphs which are too short to be summarized: %.2f %%'\
    %(len(para_too_short)/len(df_one_para[df_one_para['best_match']])*100))

Percentage of paragraphs which are too short to be summarized: 46.67 %


#### Expand: Merge Up or Down

Take one chapter into consideration, one bullet at a time. For each bullet, one paragraph is already assigned. For paragraphs which are too short compared to the bullet, merge up or down based on rouge recall of previous / next paragraph.

In [16]:
for bul in tqdm(set(df.bullets.tolist())):
    print(bul)
    df_bul = df_one_para[df_one_para['bullets'] == bul]

    book = df_bul.index.get_level_values(0)[0]
    cpt = df_bul.index.get_level_values(1)[0]

    df_bul = df_bul.reset_index()
    print(df_bul[df_bul['best_match']].para.tolist())
    best_bul_idx = np.where(df_bul['best_match'])[0][0]
    merged_para_idx = [best_bul_idx]

    bul_num_tok = df_bul.loc[best_bul_idx].bullets_num_tokens
    comp_ratio = df_bul.loc[best_bul_idx].compression_ratio
    
    print('Book %s, Chapter %s'%(book, cpt))
    print('Paragraphs in this chapter:', len(df_bul))
    print('Location of best_bul index:', best_bul_idx)
    print('Compression ratio before merging: %.2f %%'%comp_ratio)
    print()
    while comp_ratio > config.MAX_RATIO:
        if 0 in merged_para_idx:
            print('merge down')
            new_para_idx = max(merged_para_idx)+1
            df_bul.loc[new_para_idx, 'best_match'] = True
            merged_para_idx.append(new_para_idx)

        elif (len(df_bul)-1) in merged_para_idx:
            print('merge up')
            new_para_idx = min(merged_para_idx)-1
            df_bul.loc[new_para_idx, 'best_match'] = True
            merged_para_idx.append(new_para_idx)

        else:
            print('based on rouge: ', end='')

            if df_bul.loc[min(merged_para_idx)-1, config.ROUGE_TYPE_RECALL] <\
                df_bul.loc[max(merged_para_idx)+1, config.ROUGE_TYPE_RECALL]:
                print('merge down')
                new_para_idx = max(merged_para_idx)+1
                df_bul.loc[new_para_idx, 'best_match'] = True
                merged_para_idx.append(new_para_idx)
            else:
                print('merge up')
                new_para_idx = min(merged_para_idx)-1
                df_bul.loc[new_para_idx, 'best_match'] = True
                merged_para_idx.append(new_para_idx)         

        comp_ratio = bul_num_tok / np.sum(df_bul[df_bul['best_match']].para_num_tokens.tolist())
        print(df_bul[df_bul['best_match']].para.tolist())
        print('Compression ratio: %.2f %%'%comp_ratio)
        print()
        
    for p, b in zip(df_bul.loc[merged_para_idx]['para'].tolist(),
        df_bul.loc[merged_para_idx]['bullets'].tolist()):
        df_one_para.loc[(df_one_para['para'] == p) &
            (df_one_para['bullets'] == b), 'best_match'] = True
    print()

  0%|          | 3/2556 [00:00<01:35, 26.84it/s]

Epileptic syndromes are defined by clinical features, aided by appropriate investigations that include EEG and brain imaging.
['In addition to the classification of seizures, there is a separate system for epilepsies and epileptic syndromes (Table 2.2) that has been in place for many years. These are defined by groups of characteristic clinical features related to age at onset of seizures, family history of epilepsy, seizure type(s) and associated neurological symptoms and signs, aided by appropriate investigations, including EEG and brain imaging with, for example, CT and MRI (see Chapter 3, Diagnosis).']
Book 9781908541277, Chapter ch_5
Paragraphs in this chapter: 57
Location of best_bul index: 20
Compression ratio before merging: 0.23 %


Given adequate information, women can choose equally between mastectomy and breast conservation approaches.
['The indications for axillary surgery and the extent to which it should be carried out in women with operable breast cancer remain controve

  0%|          | 6/2556 [00:00<01:32, 27.61it/s]

["Pain in patients with cancer may present as various types of pain at different stages of the patient's journey with cancer. Thus, the pain may comprise acute, recurrent or chronic presentations due to the cancer and/or its treatment. Assessment of pain in patients with cancer should be the same as in other patients with pain (see Chapter 2), so that the widest possible range of treatments can be considered, with the aim of optimal treatment. Other additional symptoms such as fatigue, nausea, anxiety, depression, breathlessness and insomnia are common and also require treatment. Also, patients with cancer may have pre-existing chronic pain that continues, in addition to cancer pain (Table 9.1). Some patients with aggressive tumors may have escalating (or 'crescendo') pain requiring optimum pain management options, and the needs of cancer 'survivors' - who live for many years with chronic pain and who are increasing in numbers - also need to be addressed. Finally, patients with cancer 

  0%|          | 10/2556 [00:00<01:26, 29.31it/s]

...


There is robust evidence indicating the effectiveness of the MEND program for children and the Counterweight program for adults.
['The objective of the Counterweight program is to achieve and maintain a medically valuable weight loss of 5-10% for as many people as possible, starting with lifestyle intervention. Patients can choose between a goal-setting approach, a structured eating plan or a group program, all based on 500-600 kcal daily energy deficit. Patients also receive advice on increasing physical activity, and behavioral strategies are a core component of the model. The program is flexible and can be delivered individually or to families or groups, depending on need and resources. Nine appointments of 10-30 minutes in the first year are recommended.']
Book 9781908541680, Chapter ch_11
Paragraphs in this chapter: 35
Location of best_bul index: 14
Compression ratio before merging: 0.18 %


Disconnected tail syndrome may be associated with bulky retroperitoneal collections, panc

100%|█████████▉| 2553/2556 [01:34<00:00, 24.56it/s]


Consequence represents the severity of effect of an event.
['Consequence or harm represents the severity of the effect of the risk event should it happen, which also carries a negative connotation. The total effect of a given risk is the product of the risk and the consequence. Numerous studies have shown that people tend to pay more attention to negative consequences than positive ones, particularly when the former are seen as gruesome, refractory to treatment and poorly understood.']
Book 9781908541703, Chapter ch_3
Paragraphs in this chapter: 37
Location of best_bul index: 24
Compression ratio before merging: 0.15 %


Early life events, including compromised lung development and growth, are likely to contribute to the risk of developing COPD later.
['Exposure to other substances, including indoor and outdoor pollution, can also contribute to the development of COPD. Passive exposure to cigarette smoke is an important risk factor and may contribute to the development of COPD in non-

100%|██████████| 2556/2556 [01:34<00:00, 27.02it/s]


Amyotrophic lateral sclerosis (ALS) is not one disease, but a syndrome that overlaps with frontotemporal dementia.
["Part of the persistent confusion around nomenclature arises from an array of terms in the literature that have been inconsistently used to delineate phenotypes across the spectrum of ALS; for example, progressive muscular atrophy, primary lateral sclerosis and progressive bulbar palsy. These terms are explained later in this chapter, but 'ALS' serves well as the single unifying term for what is now understood to be a multisystem, clinically heterogeneous syndrome that overlaps pathologically and genetically with frontotemporal dementia (FTD). In relation to the most obvious symptom, ALS has understandably found itself historically classified among the neuromuscular disorders. However, for clinical, histopathological and genetic reasons, it is now more rationally considered alongside the cerebral neurodegenerative disorders (Figure 1.1)."]
Book 9781912776139, Chapter ch1

In [17]:
num_para_tot = 18822
num_para_kept = np.sum(df_one_para.groupby('para')['best_match'].apply(np.any).tolist())
print('%d out of %d paragraphs are considered using this method.'%(num_para_kept, num_para_tot), end=' ')
print('Thus, %.2f %%'%(100*num_para_kept/num_para_tot))

3747 out of 18822 paragraphs are considered using this method. Thus, 19.91 %


In [18]:
df_count_tokens = df_one_para.groupby('para', sort=False).agg({
    'best_match': lambda bm: np.any(list(bm))}).reset_index()
df_count_tokens['para_len'] = df_count_tokens.para.map(len)
num_letters_kept = df_count_tokens[df_count_tokens['best_match']].para_len.sum()
num_letters_tot = df_count_tokens.para_len.sum()

print('%d out of %d letters are considered using this method.'%(num_letters_kept, num_letters_tot), end=' ')
print('Thus, %.2f %%'%(100*num_letters_kept/num_letters_tot))

1824169 out of 6407951 letters are considered using this method. Thus, 28.47 %


In [19]:
df_count_tokens = df_one_para.groupby('para', sort=False).agg({
    'best_match': lambda bm: np.any(list(bm)),
    'para_num_tokens': lambda pnt: list(pnt)[0]})
num_tok_kept = df_count_tokens[df_count_tokens['best_match']].para_num_tokens.sum()
num_tok_tot = df_count_tokens.para_num_tokens.sum()

print('%d out of %d tokens are considered using this method.'%(num_tok_kept, num_tok_tot), end=' ')
print('Thus, %.2f %%'%(100*num_tok_kept/num_tok_tot))

377131 out of 1336051 tokens are considered using this method. Thus, 28.23 %


In [20]:
df_one_para = df_one_para[df_one_para['best_match']].reset_index().groupby(['book', 'chapter', 'bullets'], sort=False).agg({
    'para': lambda p: ' '.join(list(p)),
    'para_num_tokens': sum,
    'bullets_num_tokens': lambda bnt: list(bnt)[0]
}).reset_index(level='bullets')
df_one_para = df_one_para.rename(columns={'para': 'text'})

df_one_para['compression_ratio'] = df_one_para.bullets_num_tokens / df_one_para.para_num_tokens

In [21]:
df_one_para[df_one_para['compression_ratio'] > config.MAX_RATIO]

Empty DataFrame
Columns: [bullets, text, para_num_tokens, bullets_num_tokens, compression_ratio]
Index: []

In [22]:
para_too_short = df_one_para[df_one_para['compression_ratio'] > config.MAX_RATIO]
print('Percentage of paragraphs which are too short to be summarized: %.2f %%'\
    %(len(para_too_short)/len(df_one_para)*100))

Percentage of paragraphs which are too short to be summarized: 0.00 %


In [23]:
print(df_one_para[df_one_para['para_num_tokens'] > config.MODEL_MAX_LEN])

Empty DataFrame
Columns: [bullets, text, para_num_tokens, bullets_num_tokens, compression_ratio]
Index: []


#### Save dataset

In [24]:
df_one_para.to_csv(OUTPUT_PATH+'df.csv')

#### Create train, test, validation (CC)

In [25]:
df_one_para = df_one_para.groupby(level=[0, 1], sort=False).agg({
    'bullets': lambda b: list(b),
    'text': lambda t: list(t),
})

In [26]:
df_one_para = df_one_para.sample(frac=1, random_state=config.SEED)
df_one_para['num_bulls'] = df_one_para.bullets.map(len).cumsum()
tot_bulls = df_one_para.num_bulls.iloc[-1]
split1 = np.where(df_one_para.num_bulls > int(tot_bulls*0.8))[0][0]+1
split2 = np.where(df_one_para.num_bulls > int(tot_bulls*0.9))[0][0]+1
print(split1, split2)

361 408


In [27]:
train, val, test =\
    df_one_para.iloc[:split1].explode('bullets'),\
    df_one_para.iloc[split1:split2].explode('bullets'),\
    df_one_para.iloc[split2:].explode('bullets')

train['text'] = df_one_para.iloc[:split1].explode('text')['text']
val['text'] = df_one_para.iloc[split1:split2].explode('text')['text']
test['text'] = df_one_para.iloc[split2:].explode('text')['text']

train.to_csv(OUTPUT_PATH+'train.csv')
val.to_csv(OUTPUT_PATH+'val.csv')
test.to_csv(OUTPUT_PATH+'test.csv')

In [28]:
with open(OUTPUT_PATH+'train.source', 'w') as tr_s,\
    open(OUTPUT_PATH+'train.target', 'w') as tr_t,\
    open(OUTPUT_PATH+'train.index', 'w') as tr_i:
    for idx, row in train[['text', 'bullets']].iterrows():
        tr_i.write(str(idx) + '\n')
        tr_s.write(row.text + '\n')
        tr_t.write(row.bullets + '\n')

In [29]:
with open(OUTPUT_PATH+'val.source', 'w') as va_s,\
    open(OUTPUT_PATH+'val.target', 'w') as va_t,\
    open(OUTPUT_PATH+'val.index', 'w') as va_i:
    for idx, row in val[['text', 'bullets']].iterrows():
        va_i.write(str(idx) + '\n')
        va_s.write(row.text + '\n')
        va_t.write(row.bullets + '\n')

In [30]:
with open(OUTPUT_PATH+'test.source', 'w') as te_s,\
    open(OUTPUT_PATH+'test.target', 'w') as te_t,\
    open(OUTPUT_PATH+'test.index', 'w') as te_i:
    for idx, row in test[['text', 'bullets']].iterrows():
        te_i.write(str(idx) + '\n')
        te_s.write(row.text + '\n')
        te_t.write(row.bullets + '\n')

### **Assign Bullets to Paragraphs (Threshold)**

In [31]:
df_thresh_para = assign_highest_recall_para(df)
num_best_para = len(df_thresh_para[df_thresh_para['best_match']])

In [32]:
df_thresh_para.loc[df_thresh_para[config.ROUGE_TYPE_RECALL] > RECALL_THRESHOLD, 'best_match'] = True
num_thresh_para = len(df_thresh_para[df_thresh_para['best_match']])

In [33]:
print('Considering ONLY the best paragraph for each bullet, we keep %d paragraphs.\n'%num_best_para)
print('Considering ALSO the paragraphs with recall > %.2f, we keep %d paragraphs.'%(RECALL_THRESHOLD, num_thresh_para))
print('In the first option, we lose only %.2f %% of the information with respect to this method.'%\
    (100*(num_thresh_para-num_best_para)/num_best_para))

Considering ONLY the best paragraph for each bullet, we keep 2556 paragraphs.

Considering ALSO the paragraphs with recall > 0.70, we keep 2586 paragraphs.
In the first option, we lose only 1.17 % of the information with respect to this method.


In [34]:
df_thresh_para.loc[df_thresh_para[config.ROUGE_TYPE_RECALL] > 0.5, 'best_match'] = True
num_thresh_para_lower = len(df_thresh_para[df_thresh_para['best_match']])

print('Lowering the threshold to 0.50, we keep %d paragraphs.'%(num_thresh_para_lower))
print('In the first option, we lose %.2f %% of the information with respect to this method.\n'%\
    (100*(num_thresh_para_lower-num_best_para)/num_best_para))
print('This number is still quite low to decide to consider these paragraphs too.')

Lowering the threshold to 0.50, we keep 2943 paragraphs.
In the first option, we lose 15.14 % of the information with respect to this method.

This number is still quite low to decide to consider these paragraphs too.


### **Study Data**

In [35]:
df = pd.read_csv(OUTPUT_PATH+'df.csv').set_index(['book', 'chapter'])
df.para_num_tokens.max()

973